# **Homework 8 - Anomaly Detection**

If there are any questions, please contact mlta-2022spring-ta@googlegroups.com

Slide:    [Link]()　Kaggle: [Link](https://www.kaggle.com/c/ml2022spring-hw8)

# Set up the environment


## Package installation

In [ ]:
# Training progress bar
# !pip install -q qqdm

## Downloading data

In [ ]:
# !wget https://github.com/MachineLearningHW/HW8_Dataset/releases/download/v1.0.0/data.zip
# !kaggle competitions download -c ml2022spring-hw8

In [ ]:
# !unzip data.zip
# !unzip "ml2022spring-hw8"

# Import packages

In [ ]:
import random
import numpy as np
import torch
from torch import nn
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler, TensorDataset
import torchvision.transforms as transforms
import torch.nn.functional as F
from torch.autograd import Variable
import torchvision.models as models
from torch.optim import Adam, AdamW
from qqdm import qqdm, format_str
import pandas as pd
import os
from tqdm.auto import tqdm
import matplotlib.pyplot as plt
import torchvision
from sklearn.metrics import roc_curve, auc

# Loading data

In [ ]:

train = np.load('data/trainingset.npy', allow_pickle=True)
test = np.load('data/testingset.npy', allow_pickle=True)

print(train.shape)
print(test.shape)

## Random seed
Set the random seed to a certain value for reproducibility.

In [ ]:
def same_seeds(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if torch.cuda.is_available():
        torch.cuda.manual_seed(seed)
        torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

same_seeds(10942178)

# Autoencoder

# Models & loss

In [ ]:
class myEncoder(nn.Module):
    def __init__(self):
        super(myEncoder, self).__init__()
        # self.encoder = nn.Sequential(
        #     nn.Linear(64 * 64 * 3, 2048),
        #     nn.BatchNorm1d(2048),
        #     nn.ReLU(),
        #     nn.Linear(2048, 1024),
        #     nn.BatchNorm1d(1024),
        #     nn.ReLU(), 
        #     nn.Linear(1024, 1024),
        #     nn.BatchNorm1d(1024),
        #     nn.ReLU(), 
        #     nn.Linear(1024, 2048),
        #     nn.Sigmoid()
        # )
        self.encoder = nn.Sequential(
            nn.Conv2d(3, 64, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(64),         
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(64, 128, 4, stride=2, padding=1, bias=False),   
            nn.BatchNorm2d(128),     
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(128, 256, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(256),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(256, 512, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(512),
            nn.LeakyReLU(0.2, inplace=True),
        )
        self.to_latent = nn.Sequential(
            nn.Conv2d(512, 50, 4, stride=1, padding=0, bias=False),
            nn.BatchNorm2d(50),
            nn.LeakyReLU(0.2, inplace=True),
        )
    def forward(self, x):
        x = self.encoder(x)
        return self.to_latent(x)

class myDecoder(nn.Module):
    def __init__(self):
        super(myDecoder, self).__init__()
        # self.decoder = nn.Sequential(
        #     nn.Linear(2048, 1024),
        #     nn.BatchNorm1d(1024),
        #     nn.ReLU(),
        #     nn.Linear(1024, 1024),
        #     nn.BatchNorm1d(1024),
        #     nn.ReLU(), 
        #     nn.Linear(1024, 2048),
        #     nn.BatchNorm1d(2048),
        #     nn.ReLU(), 
        #     nn.Linear(2048, 64 * 64 * 3),
        #     nn.Tanh()
        # )
        self.decoder = nn.Sequential(
            nn.ConvTranspose2d(50, 512, 4, stride=1, padding=0, bias=False),   # from latent vector
            nn.BatchNorm2d(512),
            nn.ReLU(True),
            nn.ConvTranspose2d(512, 256, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(256), 
            nn.ReLU(True),
            nn.ConvTranspose2d(256, 128, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(128), 
            nn.ReLU(True),
            nn.ConvTranspose2d(128, 64, 4, stride=2, padding=1, bias=False),
            nn.BatchNorm2d(64), 
            nn.ReLU(True),
            nn.ConvTranspose2d(64, 3, 4, stride=2, padding=1, bias=False),
            nn.Tanh(),
        )
    def forward(self, x):
        return self.decoder(x)

In [ ]:
class NetD(nn.Module):
    """
    DISCRIMINATOR NETWORK
    """
    def __init__(self):
        super(NetD, self).__init__()
        model = myEncoder()
        layers = list(model.encoder.children())

        self.features = nn.Sequential(*layers)
        self.to_pred = nn.Sequential(
            nn.Conv2d(512, 1, 4, stride=1, padding=0, bias=False),
            nn.Sigmoid()
        )

    def forward(self, x):
        features = self.features(x)
        pred_ = self.to_pred(features)
        pred_ = pred_.view(-1)

        return pred_, features

class NetG(nn.Module):
    """
    GENERATOR NETWORK
    """

    def __init__(self):
        super(NetG, self).__init__()
        self.encoder1 = myEncoder()
        self.decoder = myDecoder()
        self.encoder2 = myEncoder()

    def forward(self, x):
        latent_i = self.encoder1(x)
        # if _noise:
        #     latent_i += latent_i * torch.randn(latent_i.shape).cuda()
        gen_imag = self.decoder(latent_i)
        latent_o = self.encoder2(gen_imag)
        return gen_imag, latent_i, latent_o

def weights_init(mod):
    """
    Custom weights initialization called on netG, netD and netE
    :param m:
    :return:
    """
    classname = mod.__class__.__name__
    if classname.find('Conv') != -1:
        mod.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        mod.weight.data.normal_(1.0, 0.02)
        mod.bias.data.fill_(0)

def reinit_d(netd):
    """ Re-initialize the weights of netD
    """
    netd.apply(weights_init)
    print('   Reloading net d')
    
def evaluate(labels, scores):
    fpr = dict()
    tpr = dict()
    roc_auc = dict()

    labels = labels.cpu()
    scores = scores.cpu()

    # True/False Positive Rates.
    fpr, tpr, _ = roc_curve(labels, scores)
    roc_auc = auc(fpr, tpr)
    return roc_auc

# Dataset module

Module for obtaining and processing data. The transform function here normalizes image's pixels from [0, 255] to [-1.0, 1.0].


In [ ]:
class CustomTensorDataset(TensorDataset):
    """TensorDataset with support of transforms.
    """
    def __init__(self, tensors):
        self.tensors = tensors
        if tensors.shape[-1] == 3:
            self.tensors = tensors.permute(0, 3, 1, 2)
        
        self.transform = transforms.Compose([
          transforms.Lambda(lambda x: x.to(torch.float32)),
          transforms.Lambda(lambda x: 2. * x/255. - 1.),
        ])
        
    def __getitem__(self, index):
        x = self.tensors[index]
        
        if self.transform:
            # mapping images to [-1.0, 1.0]
            x = self.transform(x)

        return x

    def __len__(self):
        return len(self.tensors)

# Training

## Configuration


In [ ]:
# Training hyperparameters
num_epochs = 50
batch_size = 64
learning_rate = 1e-4

# Build training dataloader
x = torch.from_numpy(train)
# train_size = int(len(x) * 0.8) 
# train_dataset = CustomTensorDataset(x[:train_size])
# val_dataset = CustomTensorDataset(x[train_size:])
train_dataset = CustomTensorDataset(x)
train_sampler = RandomSampler(train_dataset)
train_dataloader = DataLoader(train_dataset, sampler=train_sampler, batch_size=batch_size, num_workers=4)
# val_sampler = RandomSampler(val_dataset)
# val_dataloader = DataLoader(val_dataset, sampler=val_sampler, batch_size=batch_size, num_workers=4)

# build testing dataloader
eval_batch_size = 200
data = torch.tensor(test, dtype=torch.float32)
test_dataset = CustomTensorDataset(data)
test_sampler = SequentialSampler(test_dataset)
test_dataloader = DataLoader(test_dataset, sampler=test_sampler, batch_size=eval_batch_size, num_workers=4)
eval_loss = nn.MSELoss(reduction='none')

# Model
file_name = 'GANomaly'   
netd = NetD().cuda()
netg = NetG().cuda()
netg.apply(weights_init)
netd.apply(weights_init)

# Loss and optimizer
l_adv = nn.MSELoss()
l_con = nn.L1Loss()
l_enc = nn.MSELoss()
l_bce = nn.BCELoss()
criterion = nn.BCELoss()
optimizer_d = torch.optim.Adam(netd.parameters(), lr = 2e-4, betas=(0.5, 0.999))
optimizer_g = torch.optim.Adam(netg.parameters(), lr = 2e-4, betas=(0.5, 0.999))
# scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.8)
if not os.path.isdir('checkpoints'):
    os.mkdir('checkpoints')
if not os.path.isdir(f'checkpoints/{file_name}'):
    os.mkdir(f'checkpoints/{file_name}')
if not os.path.isdir(f'checkpoints/{file_name}/faces'):
    os.mkdir(f'checkpoints/{file_name}/faces')
per_train = False
if per_train:
    try:
        netd_path = f'checkpoints/{file_name}/best_netd.pt'
        netg_path = f'checkpoints/{file_name}/best_netg.pt'

        # netd.load_state_dict(torch.load(netd_path))
        netg.load_state_dict(torch.load(netg_path))
    except:
        pass

## show some image

In [ ]:
data = torch.tensor(test, dtype=torch.float32)
test_dataset = CustomTensorDataset(data)
train_sample = torch.cat([train_dataset.__getitem__(i).unsqueeze(0) for i in range(10)]).cuda()
test_sample = torch.cat([test_dataset.__getitem__(i).unsqueeze(0) for i in range(10)]).cuda()

## Training loop

In [ ]:
best_loss_D = np.inf
best_loss_G = np.inf
best_auc = 0.0
epoch_auc = 0.0
num_epochs = 50
netg.train()
netd.train()
# qqdm_train = qqdm(range(num_epochs), desc=format_str('bold', 'Description'))
for epoch in range(num_epochs):
    tot_loss_G = list()
    tot_loss_D = []
    step = 0

    for data in tqdm(train_dataloader):
        # ===================loading=====================
        img = data.float().cuda()
        bs = img.size(0)
        # ===============forward========================
        fake, latent_i, latent_o = netg(img)

        pred_real, feat_real = netd(img)
        pred_fake, feat_fake = netd(fake.detach())
        
        # =============backward=========================
        # netg
        optimizer_g.zero_grad()
        err_g_adv = l_adv(netd(img)[1], netd(fake)[1])
        err_g_con = l_con(fake, img)
        err_g_enc = l_enc(latent_o, latent_i)
        err_g = err_g_adv * 1 + err_g_con * 50 + err_g_enc * 1
        err_g.backward(retain_graph=True)
        optimizer_g.step()
        tot_loss_G += [err_g.item()]

        # netd
        optimizer_d.zero_grad()
        # Real - Fake Loss
        real_label = torch.ones (size=(bs,), dtype=torch.float32).cuda()
        fake_label = torch.zeros(size=(bs,), dtype=torch.float32).cuda()
        
        err_d_real = l_bce(pred_real, real_label)
        err_d_fake = l_bce(pred_fake, fake_label)

        # NetD Loss & Backward-Pass
        err_d = (err_d_real + err_d_fake) * 0.5
        err_d.backward()
        optimizer_d.step()
        tot_loss_D += [err_d.item()]

        if err_d.item() < 1e-5:
            print("==============================")
            reinit_d(netd)

    # scheduler.step()
    
    # # ===================show_imgs=====================
    netg.eval()
    netd.eval()
    with torch.no_grad():
        recon_imgs, _, _ = netg(test_sample)
        train_imgs, _, _ = netg(train_sample)

        grid_img = torchvision.utils.make_grid(torch.cat([train_sample.cpu(), train_imgs.cpu(), test_sample.cpu(), recon_imgs.cpu()], 0), nrow=10)
        plt.figure(figsize=(15,15))
        plt.imshow(grid_img.permute(1, 2, 0))
        plt.savefig('checkpoints/{}/faces/{}.png'.format(file_name, epoch))
        if epoch % 5 == 0 or epoch == num_epochs - 1:
            plt.show()
        plt.close()
    netg.train()
    netd.train()

    # ===================save_best====================
    mean_loss_G = np.mean(tot_loss_G)
    mean_loss_D = np.mean(tot_loss_D)
    if mean_loss_D < best_loss_D:
        best_loss_D = mean_loss_D
        torch.save(netd.state_dict(), 'checkpoints/{}/best_netd.pt'.format(file_name))
    if mean_loss_G < best_loss_G:
        best_loss_G = mean_loss_G
        torch.save(netg.state_dict(), 'checkpoints/{}/best_netg.pt'.format(file_name))
    # ===================log========================
    print(
        f'epoch {epoch + 1:.0f}/{num_epochs:.0f} | loss_G: {mean_loss_D:.5f} | loss_D: {mean_loss_G:.5f}'
    )
    # ===================save_last========================
    torch.save(netd.state_dict(), 'checkpoints/{}/epoch_{}_netd.pt'.format(file_name, epoch))
    torch.save(netg.state_dict(), 'checkpoints/{}/epoch_{}_netg.pt'.format(file_name, epoch))
torch.save(netd.state_dict(), 'checkpoints/{}/last_netd.pt'.format(file_name))
torch.save(netg.state_dict(), 'checkpoints/{}/last_netg.pt'.format(file_name))


## show images with last model
1.  original imgs
2.  reconstructed original imgs
3.  reconstructed original imgs with noises
4.  test imgs
5.  reconstructed imgs

In [ ]:
netg_path = f'checkpoints/{file_name}/epoch_2_netg.pt'
# netd.load_state_dict(torch.load(netd_path))
netg.load_state_dict(torch.load(netg_path))
# netd.eval()
netg.eval()
netg.eval()
netd.eval()
with torch.no_grad():
    latent_i = netg.encoder1(train_sample)
    latent_i += latent_i * torch.rand(latent_i.shape).cuda()
    recon_imgs = netg.decoder(latent_i)
    recon_nor, _, _ = netg(train_sample)
    recon_test, _, _ = netg(test_sample)

    grid_img = torchvision.utils.make_grid(torch.cat([train_sample, recon_nor, recon_imgs, test_sample, recon_test], 0).cpu(), nrow=10)
    x = plt.figure(figsize=(15,15))
    plt.imshow(grid_img.permute(1, 2, 0))
    # plt.savefig('123.png')
    plt.show()
    plt.close()

# Inference
Model is loaded and generates its anomaly score predictions.

## Initialize
- dataloader
- model
- prediction file

In [ ]:

# load trained model
# netd = NetD().cuda()
netg = NetG().cuda()

# netd_path = f'checkpoints/{file_name}/bset_netd.pt'
# netg_path = f'checkpoints/{file_name}/last_netg.pt'
netg_path = f'checkpoints/{file_name}/epoch_4_netg.pt'
# netd.load_state_dict(torch.load(netd_path))
netg.load_state_dict(torch.load(netg_path))
# netd.eval()
netg.eval()

# prediction file 
out_file = 'submission_ganomaly.csv'

In [ ]:
anomality = list()
with torch.no_grad():
    for i, data in enumerate(test_dataloader):
        img = data.float().cuda()
        
        fake, latent_i, latent_o = netg(img)
        preds = torch.mean(torch.pow((latent_i-latent_o), 2), dim=1)
        anomality.append(preds)

anomality = torch.cat(anomality, axis=0)
anomality = (anomality - torch.min(anomality)) / (torch.max(anomality) - torch.min(anomality))
anomality = anomality.reshape(len(test), 1).cpu().numpy()

df = pd.DataFrame(anomality, columns=['score'])
df.to_csv('probability.csv', index_label = 'ID')
df.head(10)
print(sum(anomality>0.15))

In [ ]:
plt.figure()
plt.title('prob. vs total')
plt.hist(anomality.squeeze(1), bins=50)
plt.show()